# 4 - Modelo Final e Preparação para Produção

Este notebook implementa a *versão final* de um modelo preditivo para estimar a **demanda horária** do pronto-socorro.

Os principais objetivos desta versão são:
- Definir qual o modelo será utilizado com base nas métricas utilizadas;
- Exportar o arquivo final.

Seguiremos avaliando estas etapas:
1. Seleção das features e preparação dos dados
2. Divisão treino/teste respeitando series temporais
3. Treinamento do modelo baseline (Regressão Linear)
4. Predição
5. Avaliação com MAE, RMSE, MAPE e R²
6. Gráficos de diagnóstico

---

# 1. Importar bibliotecas e configurações iniciais

### 1.0 Instalações

In [1]:
# ! pip install scikit-learn

### 1.1 Importações

In [2]:
import pandas as pd
import numpy as np
import altair as alt

In [3]:
from sklearn.model_selection import TimeSeriesSplit
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_absolute_error, r2_score, root_mean_squared_error, mean_squared_error

import locale

- Nesta etapa utilizaremos modelos lineares regularizados, que aplicam penalidades aos coeficientes para controlar a variância do modelo, reduzir overfitting e lidar com multicolinearidade.

In [4]:
from sklearn.linear_model import Ridge, Lasso, ElasticNet
from sklearn.model_selection import TimeSeriesSplit
from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import Pipeline

In [5]:
import sys
sys.path.append("../src")

from features.feature_engineering import create_lag_features, create_rolling_features, add_time_features
from training.model_evaluation import evaluate_model

In [6]:
from validation.sample_generation import generate_future_features

### 1.2 Configurações de bibliotecas

In [7]:
# Desabilitar a limitação de linhas em gráficos do Altair
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [8]:
locale.setlocale(locale.LC_ALL, 'pt_BR.UTF-8')

'pt_BR.UTF-8'

# 2. Importar e tratar dados

### 2.1 Importando dados

In [9]:
CAMINHO_DADOS = '../data/raw/dataset_pronto_socorro.csv'

df = pd.read_csv(CAMINHO_DADOS)

In [10]:
df.head()

datetime  day_of_week  month  is_weekend  temperature   rain_mm  \
0  2023-01-01 00:00:00            6      1           1    24.483571  0.353269   
1  2023-01-01 01:00:00            6      1           1    21.308678  5.847757   
2  2023-01-01 02:00:00            6      1           1    25.238443  1.141991   
3  2023-01-01 03:00:00            6      1           1    29.615149  0.524987   
4  2023-01-01 04:00:00            6      1           1    20.829233  0.820610   

   demand  
0    29.0  
1    30.0  
2    30.0  
3    33.0  
4    33.0

### 2.2 Tratamento de Dados

In [11]:
df.drop(columns=['day_of_week'], inplace=True)

In [12]:
# Converter coluna de data/hora para datetime e definir índice
if 'datetime' in df.columns:
    df['datetime'] = pd.to_datetime(df['datetime'])
    df = df.set_index('datetime')

### 2.3 Engenharia de Featurees

In [13]:
df = df.copy()

# Adicionar variáveis temporais
df = add_time_features(df)

# Lags essenciais: 1 hora, 24h, 48h, 1 semana (168h)
df = create_lag_features(df, lags=[1, 2, 3, 24, 48, 168])

# Rolling windows
df = create_rolling_features(df, windows=[3, 6, 12, 24])

# Remover linhas com NaNs causados pelos lags/rolling
df = df.dropna()

In [14]:
df.head()

month  is_weekend  temperature   rain_mm  demand  hour  \
datetime                                                                      
2023-01-08 00:00:00      1           1    20.773059  2.344874    25.0     0   
2023-01-08 01:00:00      1           1    18.231319  0.268283    25.0     1   
2023-01-08 02:00:00      1           1    17.552428  0.192845    22.0     2   
2023-01-08 03:00:00      1           1    17.920949  1.191458    34.0     3   
2023-01-08 04:00:00      1           1    21.614491  3.771095    35.0     4   

                     dayofweek  demand_lag_1  demand_lag_2  demand_lag_3  ...  \
datetime                                                                  ...   
2023-01-08 00:00:00          6          28.0          26.0          20.0  ...   
2023-01-08 01:00:00          6          25.0          28.0          26.0  ...   
2023-01-08 02:00:00          6          25.0          25.0          28.0  ...   
2023-01-08 03:00:00          6          22.0          25.0          25.0  ...   
2023-01-08 04:00:00          6          34.0          22.0          25.0  ...   

                     demand_lag_48  demand_lag_168  demand_roll_mean_3  \
datetime                                                                 
2023-01-08 00:00:00           22.0            29.0           26.333333   
2023-01-08 01:00:00           27.0            30.0           26.000000   
2023-01-08 02:00:00           24.0            30.0           24.000000   
2023-01-08 03:00:00           26.0            33.0           27.000000   
2023-01-08 04:00:00           23.0            33.0           30.333333   

                     demand_roll_std_3  demand_roll_mean_6  demand_roll_std_6  \
datetime                                                                        
2023-01-08 00:00:00           1.527525           24.166667           3.060501   
2023-01-08 01:00:00           1.732051           24.833333           2.639444   
2023-01-08 02:00:00           1.732051           24.333333           2.875181   
2023-01-08 03:00:00           6.244998           26.666667           4.082483   
2023-01-08 04:00:00           7.234178           28.166667           5.269409   

                     demand_roll_mean_12  demand_roll_std_12  \
datetime                                                       
2023-01-08 00:00:00            24.083333            3.704011   
2023-01-08 01:00:00            23.833333            3.511885   
2023-01-08 02:00:00            23.583333            3.528026   
2023-01-08 03:00:00            24.000000            4.410731   
2023-01-08 04:00:00            24.833333            5.441145   

                     demand_roll_mean_24  demand_roll_std_24  
datetime                                                      
2023-01-08 00:00:00            25.583333            3.877658  
2023-01-08 01:00:00            25.375000            3.762660  
2023-01-08 02:00:00            25.000000            3.623594  
2023-01-08 03:00:00            25.250000            4.024382  
2023-01-08 04:00:00            25.666667            4.488310  

[5 rows x 21 columns]

In [15]:
# Opcional: features sazonais contínuas (útil até pro baseline)

# Sinais "sin" e "cos" transformam hora em um ciclo contínuo, evitando que "23" esteja longe de "0".

# df['sin_hour'] = np.sin(2 * np.pi * df['hour'] / 24)
# df['cos_hour'] = np.cos(2 * np.pi * df['hour'] / 24)

# 3 Desenvolvimento de Modelo Preditivo

### 3.1 Seleção das variáveis do modelo

In [16]:
X = df.drop(columns=["temperature","rain_mm","demand"])
y = df["demand"]

In [17]:
FEATURES = X.columns.tolist()

### 3.2 Divisão dos dados em treino/teste

In [18]:
# Dividindo os dados em treino e teste, a partir da função TimseSeriesSplit, que divide os dados 
tscv = TimeSeriesSplit(n_splits=10)

### 3.3 Criação de Pipelines de treino

#### 3.3.1 Ridge

In [19]:
ridge = Pipeline([
    ("scaler", StandardScaler()),
    ("model", Ridge(alpha=1.0))
])


#### 3.3.2 Lasso

In [20]:
lasso = Pipeline([
    ("scaler", StandardScaler()),
    ("model", Lasso(alpha=0.1))
])


#### 3.3.3 ElasticNet

In [21]:
elastic = Pipeline([
    ("scaler", StandardScaler()),
    ("model", ElasticNet(alpha=0.1, l1_ratio=0.5))
])


#### 3.3.4 LinearRegression

In [22]:
linear = Pipeline([
    ("scaler", StandardScaler()),
    ("model", LinearRegression())
])


### 3.4 Validação dos modelos

In [23]:
results_ridge,df_ridge = evaluate_model(ridge, X, y, tscv)
results_lasso,df_lasso = evaluate_model(lasso, X, y, tscv)
results_enet,df_enet = evaluate_model(elastic, X, y, tscv)
results_linear,df_linear = evaluate_model(linear, X, y, tscv)

In [24]:
summary = pd.DataFrame({
    "Ridge": results_ridge.mean(),
    "Lasso": results_lasso.mean(),
    "ElasticNet": results_enet.mean(),
    "LinearRegression": results_linear.mean()
})
summary


Ridge     Lasso  ElasticNet  LinearRegression
MAE   0.010782  0.591231    1.416766      1.369946e-14
RMSE  0.013481  0.738646    1.768722      1.619783e-14
MAPE  0.054456  3.111577    7.455637      7.334416e-14
R2    0.999986  0.972107    0.840376      1.000000e+00

In [25]:
summary_df = pd.concat([df_ridge,df_lasso,df_enet,df_linear],axis=0)
summary_df.head()

model  y_true     y_pred
datetime                                       
2024-10-26 08:00:00  Ridge()    22.0  21.999549
2024-10-26 09:00:00  Ridge()    20.0  20.003481
2024-10-26 10:00:00  Ridge()    21.0  20.999191
2024-10-26 11:00:00  Ridge()    22.0  21.996030
2024-10-26 12:00:00  Ridge()    19.0  19.002495

# 4. Treinamento Final (Sem Splits)

### 4.1 Definindo qual modelo será utilizado

Com base no resultado obtido acima, pudemos notar que o modelo que obteve o melhor resultado foi a Regressão Linear.

In [26]:
best_model_name = "Ridge"
best_model = ridge

In [27]:
best_model.fit(X, y)

Pipeline(steps=[('scaler', StandardScaler()), ('model', Ridge())])

# 5. Avaliação Final (In-Sample)

In [28]:
df["pred_in_sample"] = best_model.predict(X)

### 5.1 Criar dataframe com resultados

In [29]:
df_eval = df[["demand", "pred_in_sample"]].reset_index()
df_eval["residual"] = df_eval["demand"] - df_eval["pred_in_sample"]

### 5.2 Métricas de Avaliação

In [30]:
mae = mean_absolute_error(df_eval['demand'], df_eval['pred_in_sample'])
print("MAE:", mae)

MAE: 0.004006590063813327


In [31]:
# RMSE penaliza erros grandes → ótimo para detectar picos que o modelo perdeu.
rmse = root_mean_squared_error(df_eval['demand'], df_eval['pred_in_sample'])
print("RMSE:", rmse)

RMSE: 0.00501700541883711


In [32]:
# MAPE ajuda a entender o erro percentual, mas pode distorcer quando valores são pequenos.
mape = np.mean(np.abs(df_eval["residual"] / df_eval["demand"])) * 100
print(f"MAPE: {mape:.2f}%")

MAPE: 0.02%


### 5.3 Distribuição dos Resíduos

In [33]:
# Se os resíduos não forem centrados em 0 → viés no modelo.
# Caudas pesadas → eventos extremos não capturados.

In [34]:
# Histograma
hist =alt.Chart(df_eval.reset_index()).mark_bar().encode(
    x=alt.X("residual", bin=alt.Bin(maxbins=50), title='Distribuição dos Resíduos'),
    y=alt.Y('count()',title='Frequência')
)
# Linha vertical no zero
linha_zero = (
    alt.Chart(pd.DataFrame({"x": [0]}))
    .mark_rule(color="black")
    .encode(x="x:Q")
)
# KDE (curva suavizada) — opcional
kde = (
    alt.Chart(df_eval.reset_index())
    .transform_density(
        "residual",
        as_=["residual", "density"]
    )
    .mark_line(color="red")
    .encode(
        x="residual:Q",
        y="density:Q"
    )
)

(hist + linha_zero + kde).resolve_scale(
    y="independent"
).properties(
    width=600,
    height=300,
    title="Distribuição dos resíduos"
)


alt.LayerChart(...)

### 5.4 Error por Hora do dia

- Este gráfico revela se o modelo falha no começo, meio ou final do dia.
- Se os erros forem sistematicamente altos em certas horas → falta de features temporais.

In [35]:
df_hour = df_eval.copy()
df_hour["hour"] = df_hour["datetime"].dt.hour

hour_mae = df_hour.groupby("hour",as_index=False)["residual"].apply(lambda x: np.mean(np.abs(x)))
hour_mae.head()

hour  residual
0     0  0.004669
1     1  0.004276
2     2  0.004049
3     3  0.004077
4     4  0.003868

In [36]:
chart = (
    alt.Chart(hour_mae)
    .mark_bar()
    .encode(
        x=alt.X("hour:O", title="Hora do dia"),
        y=alt.Y("residual:Q", title="Erro absoluto médio (MAE)"),
    )
    .properties(
        width=600,
        height=300,
        title="MAE por hora do dia"
    )
)

chart

alt.Chart(...)

### 5.5 Erro por dia da Semana

- A demanda hospitalar costuma variar muito entre domingo e segunda.
- Se o baseline não captura → será necessário adicionar lags.

In [37]:
df_dow = df_eval.copy()
df_dow["day_of_week"] = df_hour["datetime"].dt.day_of_week

dow_mae = df_dow.groupby("day_of_week",as_index=False)["residual"].apply(lambda x: np.mean(np.abs(x)))
dow_mae.head()

day_of_week  residual
0            0  0.004152
1            1  0.003852
2            2  0.003960
3            3  0.003907
4            4  0.003924

In [38]:
chart = (
    alt.Chart(dow_mae)
    .mark_bar()
    .encode(
        x=alt.X("day_of_week:O", title="Dia da Semana"),
        y=alt.Y("residual:Q", title="Erro absoluto médio (MAE)"),
    )
    .properties(
        width=600,
        height=300,
        title="MAE por dia da semana"
    )
)

chart

alt.Chart(...)

### 5.6 Comparação Real vs. Predição agregado por dia

- Linear Regression pode acertar nível médio mas errar amplitude.
- Se o modelo suaviza demais → pode exigir modelos não lineares.

In [39]:
df_eval.head()

datetime  demand  pred_in_sample  residual
0 2023-01-08 00:00:00    25.0       25.003637 -0.003637
1 2023-01-08 01:00:00    25.0       25.003409 -0.003409
2 2023-01-08 02:00:00    22.0       22.006924 -0.006924
3 2023-01-08 03:00:00    34.0       33.994970  0.005030
4 2023-01-08 04:00:00    35.0       34.995039  0.004961

In [40]:
df_hour = df_eval.copy()
df_hour["date"] = pd.to_datetime(df_eval['datetime'].dt.date)

daily_error = df_hour.groupby(by=["date"],as_index=False)[['demand',"pred_in_sample"]].sum()
daily_error.head()

date  demand  pred_in_sample
0 2023-01-08   649.0      649.027348
1 2023-01-09   522.0      522.020450
2 2023-01-10   543.0      542.991857
3 2023-01-11   525.0      524.998271
4 2023-01-12   515.0      515.016652

In [41]:
# Converte para formato long (necessário para múltiplas linhas no Altair)
df_long = daily_error.melt(id_vars="date", value_vars=["demand", "pred_in_sample"],
                       var_name="tipo", value_name="valor")

df_long.head()

date    tipo  valor
0 2023-01-08  demand  649.0
1 2023-01-09  demand  522.0
2 2023-01-10  demand  543.0
3 2023-01-11  demand  525.0
4 2023-01-12  demand  515.0

In [42]:
chart = (
    alt.Chart(df_long)
    .mark_line()
    .encode(
        x=alt.X("date:T", title="Data"),
        y=alt.Y("valor:Q", title="Demanda"),
        color=alt.Color("tipo:N", title="Série", scale=alt.Scale(
            domain=["demand", "pred_in_sample"],
            range=["black", "steelblue"]
        )),
        tooltip=["data:T", "tipo:N", "valor:Q"]
    )
    .properties(
        width=1200,
        height=500,
        title="Demanda diária — Real vs Prevista"
    )
)

chart

alt.Chart(...)

### 5.7 Resíduos ao longo de tempo

- Ver se há períodos em que o modelo erra sistematicamente (viés temporal).
- Ver se há heterocedasticidade (erro aumenta em períodos de pico).

In [43]:
# Linha dos resíduos
residual_line = (
    alt.Chart(df_eval.reset_index())
    .mark_line()
    .encode(
        x=alt.X("datetime:T", title="Data"),
        y=alt.Y("residual:Q", title="Resíduo")
    )
)

# Linha horizontal em zero
linha_zero = (
    alt.Chart(pd.DataFrame({"y": [0]}))
    .mark_rule(color="black")
    .encode(y="y:Q")
)

chart = (
    (residual_line + linha_zero)
    .properties(
        width=1200,
        height=400,
        title="Resíduos ao longo do tempo"
    )
)

chart

alt.LayerChart(...)

### 5.8 Interpretação dos coeficientes do modelo

- coef > 0 → aumenta demanda
- coef < 0 → reduz demanda
  
- Permite validar coerência com conhecimento hospitalar.

In [44]:
# coef_df = pd.DataFrame({
#     "feature": features,
#     "coef": model.coef_
# })

# coef_df.sort_values("coef", ascending=False)

### 5.9 Importância padronizada (coef*std)

- Isso mostra quais variáveis mais impactam a previsão na prática.
- Muito útil para justificar a evolução do modelo.

In [45]:
# stds = X_train.std()

# coef_imp_df = pd.DataFrame({
#     "feature": features,
#     "coef": model.coef_,
#     "std": stds,
# })

# coef_imp_df["importance_std"] = coef_imp_df["coef"] * coef_imp_df["std"]
# coef_imp_df.sort_values("importance_std", ascending=False)

# 6. Exportação do Modelo para Produção

Nesta etapa, salvamos o modelo para que este possa ser reutilizado.

**Por que salvar as features?**
- Para garantir consistência na produção
- Para que novos dados tenham a mesma ordem de colunas

In [46]:
FEATURES

['month',
 'is_weekend',
 'hour',
 'dayofweek',
 'demand_lag_1',
 'demand_lag_2',
 'demand_lag_3',
 'demand_lag_24',
 'demand_lag_48',
 'demand_lag_168',
 'demand_roll_mean_3',
 'demand_roll_std_3',
 'demand_roll_mean_6',
 'demand_roll_std_6',
 'demand_roll_mean_12',
 'demand_roll_std_12',
 'demand_roll_mean_24',
 'demand_roll_std_24']

In [48]:
import joblib
import os

os.makedirs("../models", exist_ok=True)

joblib.dump(best_model, "../models/model_final.pkl")
joblib.dump(FEATURES, "../models/features.pkl")

['../models/features.pkl']